In [1]:
import numpy as np
import IPython.display as ipd   # using ipd.Audio and ipd.Display to play sounds
from fractions import Fraction
import scipy.signal as sgn
import matplotlib.pyplot as plt

fs = 48000
pi = np.pi

In [2]:
sine = lambda x : np.sin(2*pi*x)
square = lambda x : sgn.square(2*pi*x)
sawtooth = lambda x : sgn.sawtooth(2*pi*x)
triangle = lambda x : sgn.sawtooth(2*pi*x,0.5)
white = lambda x : 2*np.random.rand(x.shape[0])-1

In [3]:
exp_decay = lambda L : np.exp(-np.arange(0,L,1/fs))

def ADSR(L,A=0.1,D=0.1,S=0.5,R=0.2):
    
    xp = [0,A,A+D,L,L+R]
    fp = [0,1,S,S,0]
    
    if L<A+D:
        xp.pop(2)
        fp.pop(2)
        fp[2] = (S-1)/D*(L-A)+1
    if L<A:
        xp.pop(1)
        fp.pop(1)
        fp[1] = L/A
    
    env_domain = np.arange(0,L+R,1/fs)
    env = np.interp(env_domain,xp,fp)
        
    return env

sharp_ADSR = lambda L : ADSR(L, A = 0.02, D = 0.02, S = 0.1, R = 0.02)
med_ADSR = lambda L : ADSR(L, A = 0.05, D = 0.05, S = 0.2, R = 0.1)

In [4]:
#Scales

chromatic = [1, 16/15, 9/8, 6/5, 5/4, 4/3, 25/18, 3/2, 8/5, 5/3, 9/5, 15/8]

# modes of major/minor
major = [1, 9/8, 5/4, 4/3, 3/2, 5/3, 15/8]
dorian = [1, 9/8, 6/5, 4/3, 3/2, 5/3, 9/5]
phrygian = [1, 16/15, 6/5, 4/3, 3/2, 8/5, 9/5]
lydian = [1, 9/8, 5/4, 25/18, 3/2, 5/3, 15/8]
mixolydian = [1, 9/8, 5/4, 4/3, 3/2, 5/3, 9/5]
minor = [1, 9/8, 6/5, 4/3, 3/2, 8/5, 9/5]
locrian = [1, 16/15, 6/5, 4/3, 25/18, 8/5, 9/5]

# pentatonic and blues scales
major_pent = [1, 9/8, 5/4, 3/2, 5/3]
minor_pent = [1, 6/5, 4/3, 3/2, 9/5]
major_blues = [1, 9/8, 6/5, 5/4, 3/2, 5/3]
minor_blues = [1, 6/5, 4/3, 25/18, 3/2, 9/5]

harmonic_minor = [1, 9/8, 6/5, 4/3, 3/2, 8/5, 15/8]
melodic_minor = [1, 9/8, 6/5, 4/3, 3/2, 5/3, 15/8]
whole_tone = [1, 9/8, 5/4, 25/18, 8/5, 9/5]

def pitch(degree,scale,key):
    
    deg_oct = ( degree%len(scale), degree//len(scale) )
    pitch = key * scale[deg_oct[0]] * ( 2**deg_oct[1] )
        
    return pitch

In [5]:
def bank(f,max_samps,wav_block,prints = False, graph = False):
    
    f_frac = Fraction(f).limit_denominator(20)
    cycle_frac = Fraction(fs,f_frac)
    cycle_samps = cycle_frac.numerator
    cycle_periods = cycle_frac.denominator
    
    unique_samps = min(max_samps,cycle_samps)
    
    samp_domain = np.arange(unique_samps)*float(f_frac)%fs
    
    ref_low = np.floor(samp_domain).astype(int)
    ref_high = (ref_low + 1)%fs
    decimal = samp_domain%1.0
    
    low_samps = np.take(wav_block,ref_low)
    high_samps = np.take(wav_block,ref_high)
    
    wav_chunk = low_samps*(1-decimal) + high_samps*decimal  
    
    if prints:
        print('\n f: %s \n' % f)
        print('f_frac: %s' % f_frac)
        print('samples per cycle: %s' % cycle_samps)
        print('periods per cycle: %s' % cycle_periods)
        print('max samps: %s' % max_samps)  
    
    if cycle_samps < max_samps:
        tiles = max_samps // cycle_samps + 1
        if prints:
            print('tiles: %s' % tiles)
        wav_chunk = np.tile(wav_chunk,tiles)[:max_samps]
           
    return wav_chunk

def initialize_wav_bank(FRL,wav,true_durs,L_key,prints = False):
    
    F_unique = list(set(FRL[:,0]))
    F_key = [F_unique.index(f) for f in FRL[:,0]]
       
    def long_dur(f):
        
        masked_L_key = L_key[FRL[:,0] == f]
        f_durs = [true_durs[n] for n in masked_L_key]
        
        return max(f_durs)
    
    long_durs = [long_dur(f) for f in F_unique]
     
    wav_block = wav(np.arange(0,1,1/fs))
    wav_bank = [bank(f,l,wav_block,prints) for f,l in zip(F_unique,long_durs)]
    
    return wav_bank, F_key

In [6]:
def initialize_env_bank(FRL,env):
    
    L_unique = list(set(FRL[:,2]))
    L_key = np.array([L_unique.index(l) for l in FRL[:,2]])
    
    env_bank = [env(l) for l in L_unique]
    
    return env_bank, L_key

In [7]:
def process_ins(kwargs):
    
    keys = ['F','R','L','D','key','scale','tempo','wav','env','prints']
    values = [None,None,None,[0],440,major,120,sine,ADSR,False]
    ins = dict(zip(keys, values)) 
    
    for k in keys:
        if k in kwargs:
            ins[k] = kwargs[k]

    freqs,degrees,scale,key,tempo = ins['F'],ins['D'],ins['scale'],ins['key'],ins['tempo']
    
    if not ('F' in kwargs):
        if (not ('D' in kwargs)) and ('R' in kwargs):
            freqs = np.full(len(kwargs['R']),key)
        else:
            freqs = [pitch(d,scale,key) for d in degrees]
    
    num_notes = len(freqs)
    
    if not ('R' in kwargs):
        ins['R'] = np.arange(num_notes)
    
    if not ('L' in kwargs):
        ins['L'] = np.ones(num_notes)
        
    rhythm = np.array(ins['R'])/tempo*60
    note_lengths = np.array(ins['L'])/tempo*60
        
    FRL = np.array(list(zip(freqs,rhythm,note_lengths)))
        
    return FRL, ins['wav'], ins['env'], ins['prints']

In [8]:
def main(**kwargs):
    
    FRL, wav, env, prints = process_ins(kwargs)
    
    env_bank, L_key = initialize_env_bank(FRL,env)
    true_durs = np.array([env.shape[0] for env in env_bank])
    
    wav_bank, F_key = initialize_wav_bank(FRL,wav,true_durs,L_key,prints)
    
    WE = list(zip(F_key,L_key))
    WE_unique = list(set(WE))
    WE_key = [WE_unique.index(we) for we in WE]
    
    def merge(wav_index,env_index):
        
        envelope = env_bank[env_index]
        waveform = wav_bank[wav_index]
        cut_wave = waveform[:true_durs[env_index]]
        
        return envelope * cut_wave
        
    wav_env_bank = [merge(we[0],we[1]) for we in WE_unique]
    
    starts = np.round(fs*FRL[:,1]).astype(int)
    durs = np.array([true_durs[we[1]] for we in WE])
    ends = starts + durs
    
    total_duration = max(ends)
    out = np.zeros(total_duration)
    
    for n,we in enumerate(WE):
        xs = np.arange(len(wav_env_bank[WE_key[n]]))
        ys = wav_env_bank[WE_key[n]]
        out[ starts[n] : ends[n] ] += wav_env_bank[WE_key[n]]
                
    return out

In [9]:
def mix(songs,cues= None,levels= None,tempo=120):
    
    if levels == None:
        levels = [1]*len(songs)
    if cues == None:
        cues = [0]*len(songs)
        
    cues = np.array(cues)
    
    begins = np.round(cues*60/tempo*fs).astype(int)
    finishes = [b + len(s) for b,s in zip(begins,songs)]
    
    mixed_song = np.zeros(max(finishes))
    
    for n,song in enumerate(songs):
        mixed_song[begins[n] : finishes[n]] += levels[n]*song
        
    return mixed_song

In [10]:
def loopr(r,loops,space):
    
    loop2 = sum([[n + space*m for n in r] for m in range(loops)],[])
    
    return loop2

def joinr(rs,space):
    
    return sum([[n + space*m for n in r] for m,r in enumerate(rs)],[])

def up(ds,n):
    
    return [d + n for d in ds]

In [11]:
#   A  A# B  C  C# D  D# E  F  F# G G#
#   0  1  2  3  4  5  6  7  8  9 10 11

d0 = ([0,1,2,0,0]*6 + [0,-1,-2,0,0]*2)*2
r0a = [0,3,6,10,12]
l0 = [3,3,2,2,2]*16
r0 = loopr(r0a,16,16)

d1 = ([12,7,0,1,2]*4 + [12,7,0,-1,-2]*2)*2
r1a = [14,15,16,19,22]
l1 = [1,1,3,3,2]*12
r1b = loopr(r1a,6,16)
r1 = loopr(r1b,2,128)

d2 = ([19,14,7,8,9]*2 + [19,14,7,6,5]*2)*2
r2a = [14,15,16,19,22]
l2 = [1,1,3,3,2]*8
r2b = loopr(r2a,4,16)
r2 = loopr(r2b,2,128)

f3 = [1]*32
r3 = loopr([0],32,4)
l3 = [1]*32

print(r1b)

[14, 15, 16, 19, 22, 30, 31, 32, 35, 38, 46, 47, 48, 51, 54, 62, 63, 64, 67, 70, 78, 79, 80, 83, 86, 94, 95, 96, 99, 102]


In [12]:
out0 = main(D=d0,R=r0,L=l0, scale = chromatic, env = sharp_ADSR, wav = square, tempo = 480,key = 100)
out1 = main(D=d1,R=r1,L=l1, scale = chromatic, wav = sawtooth, env = exp_decay, tempo = 480,key = 200)
out2 = main(D=d2,R=r2,L=l2, scale = chromatic, wav = sawtooth, env = exp_decay, tempo = 480,key = 200)
out3 = main(F=f3,R=r3,L=l3, wav = white, env = sharp_ADSR,tempo = 480)


out = mix([out0,out1,out2,out3],cues = [0,16,48,128],tempo = 480, levels = [0.5,0.2,0.2,1])

ipd.display(ipd.Audio(out, rate=fs))

In [57]:
#   A  A# B  C  C# D  D# E  F  F# G G#
#   0  1  2  3  4  5  6  7  8  9 10 11

D0 = [-5,7,5,3,2,0]
R0 = up([-2,0,7,8,10,12],16)
L0 = [2,7,1,2,2,4]

D1 = [0,-1,2,0,-2,3,5,7]
R1 = up([-1,0,2,4,6,8,10,12],32)
L1 = [1,2,2,2,2,2,2,2]

D2 = [0,-1,2,0,-1,0,0]
R2 = up([-1,0,2,4,6,8,12],32)
L2 = [1,2,2,2,2,2,2]

Dd = D0 + D1 + D0 + D2
Rr = R0 + R1 + up(R0,32) + up(R2,32)
Ll = L0 + L1 + L0 + L2

DD = Dd*2
RR = joinr([Rr,Rr],64)
LL = 2 * Ll

B1 = up([0,0,-5,-5,0,2,-2,3,5,7],-12)
B2 = up([0,0,-5,-5,-5,-5,2,-1,0,0],-12)

RB1 = up([0,4,8,12,16,20,22,24,26,28],16)
RB2 = up([0,4,8,12,16,18,20,22,24,28],16)

LB1 = [2,2,2,2,2,2,2,2,2,2]
LB2 = [2,2,2,2,2,2,2,2,2,2]
LB = LB1 + LB2

B = B1 + B2
RB = RB1 + up(RB2,32)








In [58]:
song1 = main(D=DD, R=RR, L= LL,scale = chromatic, env= med_ADSR, wav = triangle, tempo = 480)
song2 = main(D=B, R=RB, L= LB,scale = chromatic, env= sharp_ADSR, wav = sawtooth, tempo = 480)

song = mix([song1,song2],cues = [0,64],tempo = 480, levels = [1,0.8])

ipd.display(ipd.Audio(song, rate=fs))